<a href="https://colab.research.google.com/github/chriskenyon14/Coursera-Capstone/blob/master/CapstoneProject_FoodieVacation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [2]:
CLIENT_ID = 'BC1GLCUUKIUDYRXN3232CJLFB0UOAVWTXQ5NB3PQ5P0RZFRF' # your Foursquare ID
CLIENT_SECRET = 'BEEIFRDFFY5RFFR43ZLGEJEE5LXT0FLVP2NDC34S2GIN45KW' # your Foursquare Secret
VERSION = '20210503' # Foursquare API version

print('Your credentails:' + CLIENT_SECRET)
print('CLIENT_ID: ' + CLIENT_ID)

Your credentails:BEEIFRDFFY5RFFR43ZLGEJEE5LXT0FLVP2NDC34S2GIN45KW
CLIENT_ID: BC1GLCUUKIUDYRXN3232CJLFB0UOAVWTXQ5NB3PQ5P0RZFRF


In [3]:
#COFFEE SHOPS
LIMIT = 500 
cities = ['Jacksonville, FL','Charlotte, NC','Washington, D.C.','Boston, MA']
results = {}
for city in cities:
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&near={}&limit={}&categoryId={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        city,
        LIMIT,
        "4bf58dd8d48988d1e0931735")
    results[city] = requests.get(url).json()

In [4]:
df_venues={}
for city in cities:
    venues = json_normalize(results[city]['response']['groups'][0]['items'])
    df_venues[city] = venues[['venue.name', 'venue.location.address', 'venue.location.lat', 'venue.location.lng']]
    df_venues[city].columns = ['Name', 'Address', 'Lat', 'Lng']

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


In [5]:
maps = {}
for city in cities:
    city_lat = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lat'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lat']])
    city_lng = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lng'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lng']])
    maps[city] = folium.Map(location=[city_lat, city_lng], zoom_start=11)

    # add markers to map
    for lat, lng, label in zip(df_venues[city]['Lat'], df_venues[city]['Lng'], df_venues[city]['Name']):
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(maps[city])  
    print(f"Total number of Coffee Shops in " + city + ": ", results[city]['response']['totalResults'])

Total number of Coffee Shops in Jacksonville, FL:  119
Total number of Coffee Shops in Charlotte, NC:  139
Total number of Coffee Shops in Washington, D.C.:  191
Total number of Coffee Shops in Boston, MA:  196


In [6]:
maps[cities[0]]

In [7]:
maps[cities[1]]

In [8]:
maps[cities[2]]

In [9]:
maps[cities[3]]

In [10]:
maps = {}
for city in cities:
    city_lat = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lat'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lat']])
    city_lng = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lng'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lng']])
    maps[city] = folium.Map(location=[city_lat, city_lng], zoom_start=11)
    venues_mean_coor = [df_venues[city]['Lat'].mean(), df_venues[city]['Lng'].mean()] 
    # add markers to map
    for lat, lng, label in zip(df_venues[city]['Lat'], df_venues[city]['Lng'], df_venues[city]['Name']):
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(maps[city])
        folium.PolyLine([venues_mean_coor, [lat, lng]], color="green", weight=1.5, opacity=0.5).add_to(maps[city])
    
    label = folium.Popup("Mean Co-ordinate", parse_html=True)
    folium.CircleMarker(
        venues_mean_coor,
        radius=10,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(maps[city])

    print("Mean Distance from Coffee Shops to Mean coordinates of " + city + ": ")
    print(np.mean(np.apply_along_axis(lambda x: np.linalg.norm(x - venues_mean_coor),1,df_venues[city][['Lat','Lng']].values)))

Mean Distance from Coffee Shops to Mean coordinates of Jacksonville, FL: 
0.08964602877400975
Mean Distance from Coffee Shops to Mean coordinates of Charlotte, NC: 
0.06710007736116962
Mean Distance from Coffee Shops to Mean coordinates of Washington, D.C.: 
0.024812096893831972
Mean Distance from Coffee Shops to Mean coordinates of Boston, MA: 
0.031676902434026745


In [11]:
maps[cities[0]]

In [12]:
maps[cities[1]]

In [13]:
maps[cities[2]]

In [14]:
maps[cities[3]]

## From this information, we can conclude that the best vacation spot to visit for the purpose of tasting different coffee is Washington, DC, with a close second place going to Boston, MA, based off the information that these locations have the mose condensed options to explore.




In [15]:
#CHINESE FOOD
LIMIT = 500 
cities = ['Jacksonville, FL','Charlotte, NC','Washington, D.C.','Boston, MA']
results = {}
for city in cities:
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&near={}&limit={}&categoryId={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        city,
        LIMIT,
        "4bf58dd8d48988d145941735")
    results[city] = requests.get(url).json()

In [16]:
df_venues={}
for city in cities:
    venues = json_normalize(results[city]['response']['groups'][0]['items'])
    df_venues[city] = venues[['venue.name', 'venue.location.address', 'venue.location.lat', 'venue.location.lng']]
    df_venues[city].columns = ['Name', 'Address', 'Lat', 'Lng']

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


In [17]:
maps = {}
for city in cities:
    city_lat = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lat'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lat']])
    city_lng = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lng'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lng']])
    maps[city] = folium.Map(location=[city_lat, city_lng], zoom_start=11)

    # add markers to map
    for lat, lng, label in zip(df_venues[city]['Lat'], df_venues[city]['Lng'], df_venues[city]['Name']):
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(maps[city])  
    print(f"Total number of Chinese Restaurants in " + city + ": ", results[city]['response']['totalResults'])

Total number of Chinese Restaurants in Jacksonville, FL:  141
Total number of Chinese Restaurants in Charlotte, NC:  160
Total number of Chinese Restaurants in Washington, D.C.:  173
Total number of Chinese Restaurants in Boston, MA:  206


In [18]:
maps[cities[0]]

In [19]:
maps[cities[1]]

In [20]:
maps[cities[2]]

In [21]:
maps[cities[3]]

In [22]:
maps = {}
for city in cities:
    city_lat = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lat'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lat']])
    city_lng = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lng'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lng']])
    maps[city] = folium.Map(location=[city_lat, city_lng], zoom_start=11)
    venues_mean_coor = [df_venues[city]['Lat'].mean(), df_venues[city]['Lng'].mean()] 
    # add markers to map
    for lat, lng, label in zip(df_venues[city]['Lat'], df_venues[city]['Lng'], df_venues[city]['Name']):
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(maps[city])
        folium.PolyLine([venues_mean_coor, [lat, lng]], color="green", weight=1.5, opacity=0.5).add_to(maps[city])
    
    label = folium.Popup("Mean Co-ordinate", parse_html=True)
    folium.CircleMarker(
        venues_mean_coor,
        radius=10,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(maps[city])

    print("Mean Distance from Chinese Restaurants to Mean coordinates of " + city + ": ")
    print(np.mean(np.apply_along_axis(lambda x: np.linalg.norm(x - venues_mean_coor),1,df_venues[city][['Lat','Lng']].values)))

Mean Distance from Chinese Restaurants to Mean coordinates of Jacksonville, FL: 
0.1202470320542307
Mean Distance from Chinese Restaurants to Mean coordinates of Charlotte, NC: 
0.10150524763024053
Mean Distance from Chinese Restaurants to Mean coordinates of Washington, D.C.: 
0.03208347461585747
Mean Distance from Chinese Restaurants to Mean coordinates of Boston, MA: 
0.03302259750940025


In [23]:
maps[cities[0]]

In [24]:
maps[cities[1]]

In [25]:
maps[cities[2]]

In [26]:
maps[cities[3]]

## From this information, we can conclude that the best vacation spot to visit for the purpose of visiting different Chinese Restaurants is Washington, DC, with a second place going to Boston, MA, based off the information that these locations have the mose condensed options to explore.

In [27]:
#COFFEE SHOPS
LIMIT = 500 
cities = ['Jacksonville, FL','Charlotte, NC','Washington, D.C.','Boston, MA']
results = {}
for city in cities:
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&near={}&limit={}&categoryId={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        city,
        LIMIT,
        "4bf58dd8d48988d110941735")
    results[city] = requests.get(url).json()

In [28]:
df_venues={}
for city in cities:
    venues = json_normalize(results[city]['response']['groups'][0]['items'])
    df_venues[city] = venues[['venue.name', 'venue.location.address', 'venue.location.lat', 'venue.location.lng']]
    df_venues[city].columns = ['Name', 'Address', 'Lat', 'Lng']

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


In [29]:
maps = {}
for city in cities:
    city_lat = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lat'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lat']])
    city_lng = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lng'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lng']])
    maps[city] = folium.Map(location=[city_lat, city_lng], zoom_start=11)

    # add markers to map
    for lat, lng, label in zip(df_venues[city]['Lat'], df_venues[city]['Lng'], df_venues[city]['Name']):
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(maps[city])  
    print(f"Total number of Italian Restaurants in " + city + ": ", results[city]['response']['totalResults'])

Total number of Italian Restaurants in Jacksonville, FL:  115
Total number of Italian Restaurants in Charlotte, NC:  108
Total number of Italian Restaurants in Washington, D.C.:  151
Total number of Italian Restaurants in Boston, MA:  153


In [30]:
maps[cities[0]]

In [31]:
maps[cities[1]]

In [32]:
maps[cities[2]]

In [33]:
maps[cities[3]]

In [34]:
maps = {}
for city in cities:
    city_lat = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lat'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lat']])
    city_lng = np.mean([results[city]['response']['geocode']['geometry']['bounds']['ne']['lng'],
                        results[city]['response']['geocode']['geometry']['bounds']['sw']['lng']])
    maps[city] = folium.Map(location=[city_lat, city_lng], zoom_start=11)
    venues_mean_coor = [df_venues[city]['Lat'].mean(), df_venues[city]['Lng'].mean()] 
    # add markers to map
    for lat, lng, label in zip(df_venues[city]['Lat'], df_venues[city]['Lng'], df_venues[city]['Name']):
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            popup=label,
            color='blue',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7,
            parse_html=False).add_to(maps[city])
        folium.PolyLine([venues_mean_coor, [lat, lng]], color="green", weight=1.5, opacity=0.5).add_to(maps[city])
    
    label = folium.Popup("Mean Co-ordinate", parse_html=True)
    folium.CircleMarker(
        venues_mean_coor,
        radius=10,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(maps[city])

    print("Mean Distance from Italian Restaurants to Mean coordinates of " + city + ": ")
    print(np.mean(np.apply_along_axis(lambda x: np.linalg.norm(x - venues_mean_coor),1,df_venues[city][['Lat','Lng']].values)))

Mean Distance from Italian Restaurants to Mean coordinates of Jacksonville, FL: 
0.09574581061155486
Mean Distance from Italian Restaurants to Mean coordinates of Charlotte, NC: 
0.08440383323311255
Mean Distance from Italian Restaurants to Mean coordinates of Washington, D.C.: 
0.025343647310380066
Mean Distance from Italian Restaurants to Mean coordinates of Boston, MA: 
0.02464226177385437


In [35]:
maps[cities[0]]

In [36]:
maps[cities[1]]

In [37]:
maps[cities[2]]

In [38]:
maps[cities[3]]

## From this information, we can conclude that the best vacation spot to visit for the purpose of visiting different Italian Restaurants is Boston, MA, with a close second place going to Washington, DC, based off the information that these locations have the mose condensed options to explore.

# Based on the information from this Capstone Project, it seems like the best places to vacation based on Italian Restaurants, Chinese Restaurants, and Coffee Shops is a close call, but favors Washington, D.C. over Boston, MA by a small amount. 

# The next best place to go on vacation based on this criteria is Charlotte, NC, with the worst place (based on these selections) to go on vacation for the purpose of visiting various Restaurants being Jacksonville, FL.

In [39]:
#Italian Restaurant id: 4bf58dd8d48988d110941735 
#Chinese Restaurant id: 4bf58dd8d48988d145941735
#Coffee Shop id: 4bf58dd8d48988d1e0931735